In [1]:
import requests
from bs4 import BeautifulSoup
import time
import csv
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.common.action_chains import ActionChains
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import TimeoutException, NoSuchElementException

# URL base de las noticias de política en Newtral
BASE_URL = "https://www.newtral.es/seccion/politica/"
HEADERS = {
    'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/91.0.4472.124 Safari/537.36'
}

# Configuración del driver de Selenium
def initialize_driver():
    options = webdriver.ChromeOptions()
    options.add_argument('--headless')
    options.add_argument('--no-sandbox')
    options.add_argument('--disable-dev-shm-usage')
    return webdriver.Chrome(options=options)

driver = initialize_driver()
driver.get(BASE_URL)
wait = WebDriverWait(driver, 10)
actions = ActionChains(driver)

# Función para cargar y analizar el contenido de la página

def get_page_soup():
    page_source = driver.page_source
    return BeautifulSoup(page_source, 'html.parser')

# Función para cargar más noticias haciendo clic en el botón "Ver más"
def load_more_news():
    try:
        load_more_button = wait.until(EC.element_to_be_clickable((By.XPATH, "/html/body/main/div[2]/section[2]/div/div[2]/div")))
        actions.move_to_element(load_more_button).perform()  # Mover el cursor al botón
        time.sleep(0.5)  # Esperar medio segundo
        load_more_button.click()  # Hacer clic en el botón
        time.sleep(2)  # Esperar 2 segundos para que se carguen las nuevas noticias
    except (TimeoutException, NoSuchElementException):
        print("No se pudo encontrar o hacer clic en el botón de 'Ver más'. Puede que no haya más noticias para cargar.")
        return False
    return True

# Función para extraer detalles de cada noticia
def get_article_details(article_url):
    page_content = requests.get(article_url, headers=HEADERS).content
    if not page_content:
        return "No se encontró el título", "No se encontró la fecha", "No se encontró el contenido"

    soup = BeautifulSoup(page_content, 'html.parser')
    try:
        # Obtener el título
        title = soup.find("h1", class_="c-article__title").get_text(strip=True)

        # Obtener la fecha
        date = soup.find("time", class_="entry-date c-article__date published updated")["datetime"]

        # Obtener el contenido de la noticia excluyendo la sección de fuentes
        content_elements = soup.find_all("p", recursive=True)
        content = []
        for elem in content_elements:
            # Ignorar párrafos dentro de la sección de fuentes
            parent_section = elem.find_parent("section", class_="o-section--fact-check c-sources o-section")
            if parent_section is None:
                content.append(elem.get_text(strip=True))
        content = "\n".join(content)

        return title, date, content
    except AttributeError:
        return "No se encontró el título", "No se encontró la fecha", "No se encontró el contenido"

# Almacenar noticias
news_data = []
news_counter = 0
saved_titles = set()  # Mantener un registro de los títulos ya guardados

try:
    # Crear el archivo CSV y agregar los encabezados
    with open('noticias_newtral.csv', mode='w', newline='', encoding='utf-8') as file:
        writer = csv.writer(file)
        writer.writerow(["Número de Noticia", "Titular", "Fecha", "Contenido"])

    while True:
        # Crear el objeto BeautifulSoup a partir del contenido actual de la página
        soup = get_page_soup()

        # Obtener los enlaces de las noticias
        articles = []
        article_cards = soup.find_all("div", class_="c-card__inner")
        for card in article_cards:
            try:
                link = card.find("a", class_="c-card__title__a")
                if link and link['href'] not in saved_titles:
                    articles.append(link['href'])
            except AttributeError:
                continue

        if not articles:
            print("No se encontraron más artículos.")
            break

        for article_url in articles:
            title, date, content = get_article_details(article_url)

            # Verificar si el título ya ha sido guardado
            if title in saved_titles:
                print(f"Noticia duplicada encontrada: {title}, omitiendo...")
                continue

            news_counter += 1
            saved_titles.add(title)
            news_data.append([news_counter, title, date, content])

            # Cada 48 noticias, guardar en CSV
            if news_counter % 48 == 0:
                with open('noticias_newtral.csv', mode='a', newline='', encoding='utf-8') as file:
                    writer = csv.writer(file)
                    writer.writerows(news_data)
                news_data = []  # Limpiar datos almacenados
                print("Noticias guardadas")

        # Guardar las noticias después de cada carga
        with open('noticias_newtral.csv', mode='a', newline='', encoding='utf-8') as file:
            writer = csv.writer(file)
            writer.writerows(news_data)
        news_data = []  # Limpiar datos almacenados
        print(f"Guardadas las noticias de la página actual: {news_counter}")

        # Intentar cargar más noticias presionando el botón "Ver más"
        if not load_more_news():
            break

except Exception as e:
    print(f"Error durante la ejecución: {e}")

finally:
    # Guardar las noticias restantes
    if news_data:
        with open('noticias_newtral.csv', mode='a', newline='', encoding='utf-8') as file:
            writer = csv.writer(file)
            writer.writerows(news_data)

    # Cerrar el driver
    driver.quit()
    print("Ejecución finalizada y datos guardados correctamente.")

Guardadas las noticias de la página actual: 13
Noticia duplicada encontrada: Carles Puigdemont repetirá al frente de la presidencia de Junts para “reconstruir la mayoría independentista”, omitiendo...
Noticia duplicada encontrada: Loreto Arenillas deja su acta de diputada regional tras ser acusada de encubrir a Errejón, omitiendo...
Noticia duplicada encontrada: Así es el Grupo de Coordinación Electoral del Parlamento Europeo que acudirá a las elecciones de Georgia, omitiendo...
Noticia duplicada encontrada: Quién es Alda Recas, que reemplazará a Errejón en el escaño de Sumar en el Congreso, omitiendo...
Noticia duplicada encontrada: La Audiencia Nacional abre una investigación contra Alvise Pérez por presunta financiación ilegal de su partido político, omitiendo...
Noticia duplicada encontrada: Cayetana Álvarez de Toledo fue jefa de gabinete de Acebes (PP) en 2006, dos años después del 11-M, omitiendo...
Noticia duplicada encontrada: Del 15-M al Congreso: así ha sido la carrera políti